In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import Span
from shapely.geometry import Point
import geopandas as gpd
import glob
import bokeh
from datetime import datetime
from bokeh.layouts import column
from bokeh.models import Legend, Tabs, TabPanel
from bokeh.core.validation.warnings import MISSING_RENDERERS, EMPTY_LAYOUT

# Set fonts for matplotlib
plt.rcParams["font.family"] = "Arial"
plt.rcParams["font.size"] = 14

In [2]:

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(EMPTY_LAYOUT, True)

{Warning(code=1002, name='EMPTY_LAYOUT', description='Layout has no children')}

In [3]:
# Function to convert a pandas dataframe to a geopandas dataframe
def convert_to_gdf(df):
    geometry = [Point(xy) for xy in zip(df.longitude, df.latitude)]
    gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry=geometry)

    return gdf

# Bangladesh - Political Crisis

For this analysis the dataset utilized is: 

**Bangladesh Political Crisis Business Activity Trends Dataset**

The Political Crisis-triggered Business Activity Trends dataset contains daily data from **August 16th, 2024 to August 30th, 2024**.  

The baseline date for this dataset is **July 2nd, 2024** (45 days before the crisis).

## Purpose of this Notebook:
This notebook demonstrates the following analyses:
- **Visualizing Business Activity Data by Vertical for the National Population:**  
  Examining how different business sectors (verticals) have been impacted during and after the crisis.  
- **Analyzing Changes in Business Activity by Region and Vertical:**  
  Visualizing how trends vary across administrative regions (Admin 2) and specific business sectors. 

### Data Information Summary

This dataset provides insights into business activity at the [GADM 2](https://gadm.org/) level, covering 64 districts in Bangladesh. 

#### **Activity Quantile (activity_quantile):**
The activity quantile metric is used to measure changes in Business Activity.

- **Purpose:** Measures changes in business activity relative to a baseline period.  
- **Key Values:**
  - **0.5:** Normal activity (baseline level).  
  - **Above 0.5:** Increased activity.  
  - **Below 0.5:** Decreased activity.  

#### **Calculation Overview:**
1. Compare daily activity of business pages to their baseline activity levels (quantiles).  
2. Aggregate and standardize these values to follow a normal distribution.  
3. Apply a cumulative probability transformation to derive a value between **0 and 1**.  
4. Average results over 7 days to reduce daily noise.  
5. Provides equal weight to all businesses, avoiding bias from more active pages. 
 

In [4]:
# Read shapefiles from HdX UNOCHA
bgd_adm2 = gpd.read_file(
    "../../data/bgd_adm_bbs_20201113_SHP/bgd_admbnda_adm2_bbs_20201113.shp"
)
bgd_adm1 = gpd.read_file(
    "../../data/bgd_adm_bbs_20201113_SHP/bgd_admbnda_adm1_bbs_20201113.shp"
)

c:\Users\wb614536\.conda\envs\env_bgd\Lib\site-packages\pyogrio\core.py:35: RuntimeWarning: Could not detect GDAL data files.  Set GDAL_DATA environment variable to the correct path.
  _init_gdal_data()


In [5]:
# Read the business activity data
# Crisis related
all_files = glob.glob("../../data/business-activity-trends/raw/aug-2024/*.csv")

businessActivity2024 = pd.DataFrame(
    columns=[
        "polygon_id",
        "polygon_name",
        "polygon_level",
        "polygon_version",
        "country",
        "business_vertical",
        "activity_quantile",
        "latitude",
        "longitude",
        "ds",
    ]
)

li = []

for file in all_files:
    df1 = pd.read_csv(file)
    li.append(df1)

# Concatenate all the data into one DataFrame
businessActivity2024 = pd.concat(li, axis=0)
businessActivity2024 = businessActivity2024[businessActivity2024["country"] == "BD"]

# Convert columns to datetime
businessActivity2024["ds"] = businessActivity2024["ds"].apply(
    lambda x: pd.to_datetime(x)
)

In [6]:
# Get the unique business verticals 
business_verticals = list(businessActivity2024["business_vertical"].unique())

print(
    f"Bangladesh Political Crisis Business Actvity Trends has the following business verticals {business_verticals}"
)

Bangladesh Political Crisis Business Actvity Trends has the following business verticals ['Local Events', 'Business & Utility Services', 'Retail', 'Restaurants', 'Public Good', 'Professional Services', 'Home Services', nan, 'Travel', 'Grocery & Convenience Stores', 'Lifestyle Services', 'All', 'Manufacturing']


In [7]:
from bokeh.models import Div, Span, Label
from bokeh.layouts import column

def get_line_plot(
    businessActivity,
    title,
    source,
    subtitle=None,
    vertical_dates=None,
    vertical_labels=None,
    limitations_note=None,  # Add note parameter
    label_offset=10  # Offset for labels to the right
):
    # Create the main figure
    p2 = figure(
        x_axis_type="datetime", 
        width=1000, 
        height=600, 
        toolbar_location="above",
        sizing_mode="stretch_width"  
    )
    p2.add_layout(Legend(), "right")

    # Define a color palette 
    from bokeh.palettes import Category20
    color_palette = Category20[15]  

    # Plot lines for each business vertical
    for id, business_vertical in enumerate(businessActivity["business_vertical"].unique()):
        if pd.isnull(business_vertical):  # Handle missing values in business_vertical
            business_vertical = "Unknown"

        business_vertical = str(business_vertical)  # Ensure it's a string

        df = businessActivity[businessActivity["business_vertical"] == business_vertical][
            ["ds", "activity_quantile"]
        ].reset_index(drop=True)

        p2.line(
            df["ds"],
            df["activity_quantile"],
            line_width=2,
            line_color=color_palette[id % len(color_palette)],  # Handle color overflow
            legend_label=business_vertical,
        )

    # Configure legend
    p2.legend.click_policy = "hide"
    p2.legend.label_text_font_size = "10pt"

    # Horizontal line at 0.5
    baseline = Span(
        location=0.5, 
        dimension="width", 
        line_color="black", 
        line_dash="dashed", 
        line_width=2
    )
    p2.add_layout(baseline)

    # Add vertical lines and labels if provided
    if vertical_dates and vertical_labels:
        for date, label_text in zip(vertical_dates, vertical_labels):
            vline = Span(location=date.timestamp() * 1000, 
                         dimension="height", 
                         line_color="grey", 
                         line_width=1.5, 
                         line_dash="dashed")
            
            p2.add_layout(vline)
            
            label = Label(
                x=date.timestamp() * 1000 + label_offset,  # Adjust to the right
                y=0.7,  # Example y position, adjust as needed
                text=label_text,
                text_color="grey",
                text_font_size="7pt"
            )
            p2.add_layout(label)

    # Use Div for title and subtitle
    title_div = Div(
        text=f"<h2>{title}</h2>", 
        styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"}
    )
    subtitle_div = Div(
        text=f"<p><em>{subtitle}</em></p>" if subtitle else "",
        styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"}
    )
    source_div = Div(
        text=f"<p><small>{source}</small></p>",
        styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"}
    )

    # Add limitations note if provided
    note_div = None
    if limitations_note:
        note_div = Div(
            text=f"""
            <div style="
                background-color: #f9f9f9; 
                border: 1px solid #dddddd; 
                padding: 10px; 
                border-radius: 5px;
                font-size: 12pt;
                margin-top: 10px;
                max-width: 800px;  /* Limit the width of the note */
                word-wrap: break-word;  /* Ensure text wraps within the width */
            ">
                <strong>Note:</strong> {limitations_note}
            </div>
            """,
        )

    # Combine all elements
    layout_elements = [title_div, subtitle_div, p2, source_div]
    if note_div:
        layout_elements.append(note_div)

    layout = column(*layout_elements)

    return layout


### Visualizing Business Activity Data by Vertical 

In [8]:
from bokeh.models import Div, Panel, Tabs
from bokeh.plotting import output_notebook, show
from bokeh.layouts import column

# Activate notebook output
output_notebook()

# Taking the mean activity quantile for the entire country to allow for comparison with last year's data
df = (
    businessActivity2024.groupby(["country", "business_vertical", "ds"])
    .mean("activity_quantile")[["activity_quantile"]]
    .reset_index()
)


# Create a how to read it tab
def get_explanation_tab():
    """Create a tab explaining how to read the chart."""
    title_div = Div(
        text="<h2>How to read it?</h2>",
        styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"}
    )
    
    explanation_div = Div(
        text="""
        <p>This chart visualizes <strong>Business Activity Trends</strong> during the Bangladesh crisis compared to a 45-day pre-crisis baseline. 
        The metric used is the <em>Activity Quantile</em>, which compares daily activity levels to the baseline period.</p>
        <p><strong>Key Interpretation:</strong></p>
        <ul>
          <li>A value of <strong>0.5</strong> represents <em>normal</em> or <em>baseline-like</em> activity levels, typical of the pre-crisis period.</li>
          <li>Values <strong>above 0.5</strong> indicate increased business activity, showing a higher level of posts compared to the baseline.</li>
          <li>Values <strong>below 0.5</strong> indicate decreased business activity, suggesting lower activity levels relative to the baseline.</li>
        </ul>
        <p>The horizontal dashed line at <strong>0.5</strong> serves as a reference point for normal activity. Any significant deviation from this line highlights anomalous trends in business activity.</p>
        <p>Each colored line represents a different business vertical, allowing a comparative view of sectoral impacts during the crisis.</p>
        <hr>
        <p><strong>Limitations:</strong></p>
        <p>This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. 
        The methodology assumes that businesses post more frequently on Facebook when they are open and less frequently when they are closed. While this allows for insights into disruptions and recovery patterns, these assumptions may not hold true in all contexts. 
        For example, if businesses are posting about the ongoing crisis rather than regular operations, this could be interpreted as increased activity, potentially leading to misleading conclusions about their operational status.</p>
        """,
        styles={"text-align": "left", "font-size": "12pt"}
    )
    
    layout = column(title_div, explanation_div)
    return layout


# Create the tabs
tabs = []

# Tab 1: Political Crisis
tabs.append(
    TabPanel(
        child=get_line_plot(
            df, 
            "Business Activity (Aug 16 2024 - Aug 30 2024)",
            "Source: Data for Good, Meta",
            subtitle="National average during the Bangladesh crisis compared to 45 days prior baseline (July 2nd, 2024)", 
            limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
        ),
        title="Political Crisis-Triggered",
    )
)

# Add the explanation tab
tabs.append(
    TabPanel(
        child=get_explanation_tab(),
        title="How to read it?",
    )
)

# Display the tabs
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)





Loading BokehJS ...

In [9]:
import unicodedata

# Normalize and standardize polygon names in activity data
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].apply(
    lambda x: x.upper() if isinstance(x, str) else x
)
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].apply(
    lambda x: unicodedata.normalize("NFD", x).encode("ascii", "ignore").decode("utf-8")
)

# Rename columns from shapefile to match activity data
bgd_adm2 = bgd_adm2.rename(columns={"ADM2_EN": "polygon_name"})
bgd_adm2["polygon_name"] = bgd_adm2["polygon_name"].str.upper()


# Match districts between activity data and shapefile
matched_districts = list(
    set(businessActivity2024["polygon_name"].unique()).intersection(
        set(bgd_adm2["polygon_name"].unique())
    )
)

# Identify and print unmatched districts
unmatched_districts = list(
    businessActivity2024[~businessActivity2024["polygon_name"].isin(matched_districts)][
        "polygon_name"
    ].unique()
)
print("Unmatched districts:", unmatched_districts)

print(
    "There are no districts unmapped."
)




Unmatched districts: []
There are no districts unmapped.


### Analyzing Changes in Business Activity by Region and Vertical

In [10]:
# Add a temporary key  datasets
bgd_adm2["key"] = 1  # Adding a key for Cartesian join
businessActivity2024["key"] = 1  # Adding a key for Cartesian join

# political crisis
# Perform Cartesian join
bgd_adm2_repeated = pd.merge(
    bgd_adm2.drop(columns=["geometry"]),  # Drop geometry temporarily for the join
    businessActivity2024,
    on=["key", "polygon_name"],  # Use the shared key for Cartesian product
    how="inner"
)

# Restore geometry column
bgd_adm2_repeated = pd.merge(
    bgd_adm2_repeated,
    bgd_adm2[["polygon_name", "geometry"]],
    on="polygon_name",
    how="left"
)

# Convert back to GeoDataFrame
bgd_adm2_merged = gpd.GeoDataFrame(bgd_adm2_repeated, geometry="geometry", crs=bgd_adm2.crs)


In [11]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64

# Create a function to generate map plot

def map_plot(data, date, title=None, source=None, subtitle=None):
    # Filter the data for the selected date
    data_for_date = data[data["ds"] == date]

    # Set up the color map and normalization
    cmap = cm.RdYlGn  # Red for below 0.5, green for above
    norm = TwoSlopeNorm(vmin=0, vcenter=0.5, vmax=1)

    # Create the figure and axis
    fig, ax = plt.subplots(figsize=(7, 3))

    # Plot boundaries and the data
    data_for_date.boundary.plot(ax=ax, linewidth=0.5, color="white")  # Plot boundaries
    data_for_date.plot(
        column="activity_quantile",
        cmap=cmap,
        norm=norm,
        linewidth=0.8,
        ax=ax,
        edgecolor="white",
        legend=True,
        legend_kwds={"label": "Activity Quantile", "orientation": "vertical"},
    )

    # Add title, subtitle, and source if provided
    if title:
        ax.set_title(title, fontsize=14, fontweight="bold")
    if subtitle:
        fig.text(0.5, 0.93, subtitle, ha='center', fontsize=12, style='italic')
    if source:
        fig.text(0.5, 0.01, source, ha='center', fontsize=10, style='italic')

    # Customize the plot
    ax.axis("off")  # Turn off axis

    # Save the plot to a BytesIO object
    buf = BytesIO()
    plt.savefig(buf, format="png", bbox_inches="tight")
    plt.close(fig)
    buf.seek(0)

    # Encode the image to base64
    img_base64 = base64.b64encode(buf.read()).decode("utf-8")
    buf.close()

    return img_base64


#### Bangladesh Political Crisis Business Activity Trends Dataset

This map visualizes **business activity trends** during the aftermath of the political crisis in Bangladesh, allowing insights into mobility and recovery in these affected areas. 

**Key Insights from the July-August 2024 Political Crisis**

The crisis in July-August 2024 caused significant disruptions nationwide, including curfews, internet shutdowns, governmental transitions, and local unrest in critical areas. Below are the key insights:

**Key Dates:**
- **July 17, 2024**: [Internet services were shut down nationwide](https://www.reuters.com/world/asia-pacific/bangladeshs-internet-shutdown-isolates-citizens-disrupts-business-2024-07-26/) 
- **July 19, 2024**: [Curfews were imposed across major cities](https://www.bbc.com/news/articles/cl4ymjrx10xo) 
- **August 5, 2024**: [The Prime Minister announced their resignation](https://www.washingtonpost.com/world/2024/08/05/bangladesh-prime-minister-hasina-resigns/) 
- **August 8, 2024**: [A transition government was formed](https://www.aljazeera.com/news/2024/8/8/muhammad-yunus-takes-oath-as-head-of-bangladeshs-interim-government)

**Key Places:**
- Major cities like **Dhaka, Chattogram, and Sylhet** experienced economic and mobility disruptions due to curfews and political instability.
- **Narsingdi District**: [Site of significant unrest, including a high-profile prison outbreak](https://www.bbc.com/news/articles/cl4ymjrx10xo).
- Widespread restrictions affected administrative districts and urban centers.



In [12]:
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook, show

# Activate notebook output
output_notebook()

def get_map_tab(data, date, title, source, subtitle=None):
    # Get the base64 image string from the map_plot function
    img_base64 = map_plot(data, date)
    
    # Create Div elements for title, subtitle, and source
    title_div = Div(
        text=f"<h2>{title}</h2>",
        styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"}
    )
    subtitle_div = Div(
        text=f"<p><em>{subtitle}</em></p>" if subtitle else "",
        styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"}
    )
    source_div = Div(
        text=f"<p><small>{source}</small></p>",
        styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"}
    )
    
    # Create the image Div
    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)
    
    # Combine all elements into a layout
    layout = column(title_div, subtitle_div, img_div, source_div)
    
    return layout

def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(
        text="<h2>How to read it?</h2>",
        styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"}
    )
    
    explanation_div = Div(
        text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during the Bangladesh crisis compared to a 45-day pre-crisis baseline.</p>
        <p><strong>Key Interpretation:</strong></p>
        <ul>
          <li>The colors on the map represent the <em>Activity Quantile</em>, which measures business activity relative to the baseline period.</li>
          <li>A value of <strong>0.5</strong> (shown near the midpoint of the color bar) indicates normal activity levels typical of the baseline.</li>
          <li>Values <strong>above 0.5</strong> (closer to green) indicate increased activity levels.</li>
          <li>Values <strong>below 0.5</strong> (closer to red) indicate decreased activity levels.</li>
        </ul>
        <p>Each polygon represents a geographical area. Business activity levels are aggregated for all businesses within that area.</p>
        <p>The horizontal legend bar helps in identifying the relative activity quantile of each area, making it easier to spot regions with anomalous activity levels.</p>
        <hr>
        <p><strong>Limitations:</strong></p>
        <p>This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. 
        The methodology assumes that businesses post more frequently on Facebook when they are open and less frequently when they are closed. While this allows for insights into disruptions and recovery patterns, these assumptions may not hold true in all contexts. 
        For example, if businesses are posting about the ongoing crisis rather than regular operations, this could be interpreted as increased activity, potentially leading to misleading conclusions about their operational status.</p>
        """,
        styles={"text-align": "left", "font-size": "12pt"}
    )
    
    layout = column(title_div, explanation_div)
    return layout

# Define the selected dates and create tabs
selected_dates = ["2024-08-16", "2024-08-20","2024-08-21",  "2024-08-25","2024-08-27",  "2024-08-30"]
tabs = []

for date in selected_dates:
    # Add a tab for each date
    tabs.append(
        TabPanel(
            child=get_map_tab(
                bgd_adm2_merged,
                date=date,
                title=f"Business Activity (Political crisis-triggered) on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline (July 2nd, 2024) during the Bangladesh Political crisis"
            ),
            title=date
        )
    )

# Add the explanation tab
tabs.append(
    TabPanel(
        child=get_explanation_tab(),
        title="How to read it?"
    )
)

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")

# Show the tabs
show(tabs_layout)



Loading BokehJS ...